# Endpoint Flow Testing
### Dataset: Movie Lens
### Algorithm: Time Aware ItemKNN Incremental
### Padding Method: Popularity

In [1]:
import pandas as pd

In [2]:
from streamsightv2.algorithms import TARSItemKNNLiu
external_model = TARSItemKNNLiu(K=100)

INFO - streamsight package loaded.
WARNING - /Users/joshua/projects/fyp/streamsightv2/venv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm



In [3]:
# Replace with actual stream_id and algorithm_id
stream_id =  "9072052c-4e08-4a50-9f51-e6b3f511d741"
algorithm_id = "bdd640fb-0667-4ad1-9c80-317fa3b1799d"

# Iteration 1

In [4]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/training-data"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
print(response.status_code)
print(response.content)
training_df = pd.DataFrame(response.json().get('training_data'))
shape = response.json().get('shape')


http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/training-data
200
b'{"shape":[413,1415],"training_data":[{"interactionid":0,"uid":0,"iid":0,"ts":874724710},{"interactionid":1,"uid":0,"iid":1,"ts":874724727},{"interactionid":2,"uid":0,"iid":2,"ts":874724754},{"interactionid":3,"uid":0,"iid":3,"ts":874724781},{"interactionid":4,"uid":0,"iid":4,"ts":874724843},{"interactionid":5,"uid":0,"iid":5,"ts":874724882},{"interactionid":6,"uid":0,"iid":6,"ts":874724882},{"interactionid":7,"uid":0,"iid":7,"ts":874724905},{"interactionid":8,"uid":0,"iid":8,"ts":874724937},{"interactionid":9,"uid":0,"iid":9,"ts":874724988},{"interactionid":10,"uid":0,"iid":10,"ts":874725081},{"interactionid":11,"uid":0,"iid":11,"ts":874725120},{"interactionid":12,"uid":0,"iid":12,"ts":874725264},{"interactionid":13,"uid":0,"iid":13,"ts":874725386},{"interactionid":14,"uid":0,"iid":14,"ts":874725485},{"interactionid":15,"uid":0,"iid":15,"ts":874725485},

In [5]:
from streamsightv2.matrix import InteractionMatrix

training_im = InteractionMatrix(training_df, item_ix='iid', user_ix='uid', timestamp_ix='ts', shape=shape)
external_model.fit(training_im)

X after decay:  [[2.70997488e-30 2.71050814e-30 2.71135531e-30 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00 3.07621947e-25 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 ...
 [6.95081029e-01 6.89608010e-01 6.95435096e-01 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 7.76937140e-01 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [9.68134496e-01 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 9.51647881e-01]]
DEBUG - Fitting TARSItemKNNLiu complete - Took 0.173s


TARSItemKNNLiu(K=100)

In [6]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/unlabeled-data"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
ul_df = pd.DataFrame(response.json().get('unlabeled_data'))
shape = response.json().get('shape')
ul_df

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/unlabeled-data


interactionid  uid  iid         ts
0             39235  412   -1  880606923
1             39236  412   -1  880606923
2             39237  412   -1  880606947
3             39238  412   -1  880606993
4             39239  412   -1  880606993
...             ...  ...  ...        ...
7579          50929  500   -1  883195456
7580          50930  500   -1  883195456
7581          50931  500   -1  883195479
7582          50932  500   -1  883195527
7583          50933  500   -1  883195527

[7584 rows x 4 columns]

In [9]:
ul_im = InteractionMatrix(ul_df, item_ix='iid', user_ix='uid', timestamp_ix='ts', shape=shape)
prediction = external_model.predict(training_im, ul_im)
print(prediction.toarray())
matrix_dict = {
    'data': prediction.data.tolist(),
    'indices': prediction.indices.tolist(),
    'indptr': prediction.indptr.tolist(),
    'shape': prediction.shape
}




DEBUG - Performing items_in comparison


In ItemKNNIncremental _predict:  [[2.79404064e-14 1.90314480e-14 1.06805178e-30 ... 0.00000000e+00
  0.00000000e+00 4.65959897e-14]
 [3.34234696e-11 3.05479507e-11 3.54826876e-11 ... 3.09916261e-25
  0.00000000e+00 7.78473204e-24]
 [1.92942901e-22 2.89795954e-29 1.44127980e-29 ... 8.24588680e-23
  0.00000000e+00 1.27919765e-22]
 ...
 [2.18028151e+01 1.67936742e+01 1.40695419e+01 ... 0.00000000e+00
  0.00000000e+00 5.46374860e+00]
 [4.21540446e+00 1.48908893e+01 2.10738817e+00 ... 3.06221825e-01
  0.00000000e+00 1.96967812e+00]
 [4.90079596e+01 2.55342535e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 1.07230826e+02]]
Max user ID:  501
Max item ID:  0
X.shape:  [413, 1415]
Intended shape:  (501, 1415)
Predict frame:        interactionid  uid  iid         ts  interactionid
0                 0  412   -1  880606923          39235
1                 1  412   -1  880606923          39236
2                 2  412   -1  880606947          39237
3                 3  412   -1  880606993  

In [10]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/predictions"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.post(url, json=matrix_dict)
print(response.status_code)
print(response.content)

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/predictions
200
b'{"status":true}'


In [11]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/is-completed"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
print(response.content)

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/is-completed
b'false'


In [12]:

## Iteration 2

In [13]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/training-data"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
print(response.status_code)
print(response.content)
training_df = pd.DataFrame(response.json().get('training_data'))
shape = response.json().get('shape')

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/training-data
200
b'{"shape":[501,1470],"training_data":[{"interactionid":39235,"uid":412,"iid":262,"ts":880606923},{"interactionid":39236,"uid":412,"iid":407,"ts":880606923},{"interactionid":39237,"uid":412,"iid":848,"ts":880606947},{"interactionid":39238,"uid":412,"iid":337,"ts":880606993},{"interactionid":39239,"uid":412,"iid":583,"ts":880606993},{"interactionid":39240,"uid":412,"iid":99,"ts":880606993},{"interactionid":39241,"uid":412,"iid":289,"ts":880607034},{"interactionid":39242,"uid":412,"iid":613,"ts":880607116},{"interactionid":39243,"uid":412,"iid":976,"ts":880607154},{"interactionid":39244,"uid":412,"iid":486,"ts":880607154},{"interactionid":39245,"uid":412,"iid":488,"ts":880607154},{"interactionid":39246,"uid":412,"iid":1001,"ts":880607154},{"interactionid":39247,"uid":412,"iid":443,"ts":880607205},{"interactionid":39248,"uid":412,"iid":766,"ts":880607231},{"

In [14]:
from streamsightv2.matrix import InteractionMatrix

training_im = InteractionMatrix(training_df, item_ix='iid', user_ix='uid', timestamp_ix='ts', shape=shape)
external_model.fit(training_im)

X after decay:  [[2.63605636e-43 2.63657508e-43 2.63739914e-43 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 5.81380671e-01 2.99231111e-38 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 ...
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]]
DEBUG - Fitting TARSItemKNNLiu complete - Took 0.152s


TARSItemKNNLiu(K=100)

In [15]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/unlabeled-data"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
ul_df = pd.DataFrame(response.json().get('unlabeled_data'))
shape = response.json().get('shape')
ul_df

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/unlabeled-data


interactionid  uid  iid         ts
0             50934  501   -1  883215358
1             50935  501   -1  883215406
2             50936  501   -1  883215406
3             50937  501   -1  883215525
4             50938  501   -1  883215586
...             ...  ...  ...        ...
9330          64471  490   -1  885784518
9331          64472  490   -1  885784558
9332          64473  490   -1  885784558
9333          64474  490   -1  885784558
9334          64475  490   -1  885784583

[9335 rows x 4 columns]

In [16]:
ul_im = InteractionMatrix(ul_df, item_ix='iid', user_ix='uid', timestamp_ix='ts', shape=shape)
prediction = external_model.predict(training_im, ul_im)
print(prediction.toarray())
matrix_dict = {
    'data': prediction.data.tolist(),
    'indices': prediction.indices.tolist(),
    'indptr': prediction.indptr.tolist(),
    'shape': prediction.shape
}

DEBUG - Performing items_in comparison
In ItemKNNIncremental _predict:  [[8.02773994e-44 0.00000000e+00 2.18266738e-43 ... 5.93214709e-27
  5.93214709e-27 1.74297772e-43]
 [2.94498161e-37 3.92482477e+00 7.46789266e-02 ... 1.12881604e-01
  1.12881604e-01 1.99357328e-38]
 [5.25708293e-42 1.36281214e-43 5.60941554e-42 ... 1.22217558e-35
  1.22217558e-35 0.00000000e+00]
 ...
 [6.26659144e-02 9.64013417e-02 5.88568501e-02 ... 2.22376450e-03
  2.22376450e-03 6.50851734e-02]
 [0.00000000e+00 0.00000000e+00 3.27277537e-02 ... 2.46483158e-01
  2.46483158e-01 4.01924349e-04]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 1.87575851e-01
  3.74712623e-01 0.00000000e+00]]
Max user ID:  633
Max item ID:  0
X.shape:  [501, 1470]
Intended shape:  (633, 1470)
Predict frame:        interactionid  uid  iid         ts  interactionid
0                 0  501   -1  883215358          50934
1                 1  501   -1  883215406          50935
2                 2  501   -1  883215406          50936
3  

In [17]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/predictions"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.post(url, json=matrix_dict)
print(response.status_code)
print(response.content)

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/predictions
200
b'{"status":true}'


In [18]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/is-completed"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
print(response.content)

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/is-completed
b'false'


## Iteration 3


In [19]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/training-data"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
print(response.status_code)
print(response.content)
training_df = pd.DataFrame(response.json().get('training_data'))
shape = response.json().get('shape')

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/training-data
200
b'{"shape":[633,1562],"training_data":[{"interactionid":50934,"uid":501,"iid":119,"ts":883215358},{"interactionid":50935,"uid":501,"iid":301,"ts":883215406},{"interactionid":50936,"uid":501,"iid":303,"ts":883215406},{"interactionid":50937,"uid":501,"iid":1332,"ts":883215525},{"interactionid":50938,"uid":501,"iid":305,"ts":883215586},{"interactionid":50939,"uid":501,"iid":998,"ts":883215586},{"interactionid":50940,"uid":501,"iid":1007,"ts":883215630},{"interactionid":50941,"uid":501,"iid":381,"ts":883215630},{"interactionid":50942,"uid":501,"iid":302,"ts":883215630},{"interactionid":50943,"uid":501,"iid":994,"ts":883215660},{"interactionid":50944,"uid":501,"iid":307,"ts":883215723},{"interactionid":50945,"uid":501,"iid":121,"ts":883215723},{"interactionid":50946,"uid":501,"iid":223,"ts":883215723},{"interactionid":50947,"uid":501,"iid":120,"ts":883215723},

In [20]:
from streamsightv2.matrix import InteractionMatrix

training_im = InteractionMatrix(training_df, item_ix='iid', user_ix='uid', timestamp_ix='ts', shape=shape)
external_model.fit(training_im)

X after decay:  [[2.55222182e-56 2.55272404e-56 2.55352189e-56 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 5.62891012e-14 2.89714659e-51 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 ...
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 9.01502801e-01 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 9.04994522e-01]]
DEBUG - Fitting TARSItemKNNLiu complete - Took 0.261s


TARSItemKNNLiu(K=100)

In [21]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/unlabeled-data"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
ul_df = pd.DataFrame(response.json().get('unlabeled_data'))
shape = response.json().get('shape')
ul_df

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/unlabeled-data


interactionid  uid  iid         ts
0             64476   47   -1  885804123
1             64477   47   -1  885805093
2             64478   47   -1  885805554
3             64479  633   -1  885806710
4             64480  633   -1  885806710
...             ...  ...  ...        ...
6683          75252  711   -1  888351713
6684          75253  711   -1  888351713
6685          75254  711   -1  888351813
6686          75301  372   -1  888364663
6687          75302  372   -1  888364663

[6688 rows x 4 columns]

In [22]:
ul_im = InteractionMatrix(ul_df, item_ix='iid', user_ix='uid', timestamp_ix='ts', shape=shape)
prediction = external_model.predict(training_im, ul_im)
print(prediction.toarray())
matrix_dict = {
    'data': prediction.data.tolist(),
    'indices': prediction.indices.tolist(),
    'indptr': prediction.indptr.tolist(),
    'shape': prediction.shape
}

DEBUG - Performing items_in comparison
In ItemKNNIncremental _predict:  [[4.83982138e-13 7.61724708e-13 1.28612905e-13 ... 0.00000000e+00
  0.00000000e+00 8.16008763e-13]
 [6.29449877e-44 5.92864806e-09 2.50570407e-09 ... 1.58199343e-50
  2.28369128e-50 1.98545968e-13]
 [6.12354928e-55 4.17469705e-56 2.25513613e-55 ... 2.53256079e-54
  2.29861385e-48 0.00000000e+00]
 ...
 [1.80113517e-01 1.02342981e+00 7.52249545e-05 ... 0.00000000e+00
  0.00000000e+00 4.10788783e-01]
 [7.23429479e-01 9.95071876e-01 1.56353123e-01 ... 0.00000000e+00
  0.00000000e+00 8.58115106e-01]
 [4.12407806e-01 1.36990580e+01 8.14152675e-01 ... 0.00000000e+00
  0.00000000e+00 1.57855502e+01]]
Max user ID:  712
Max item ID:  0
X.shape:  [633, 1562]
Intended shape:  (712, 1562)
Predict frame:        interactionid  uid  iid         ts  interactionid
0                 0   47   -1  885804123          64476
1                 1   47   -1  885805093          64477
2                 2   47   -1  885805554          64478
3  

In [23]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/predictions"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.post(url, json=matrix_dict)
print(response.status_code)
print(response.content)

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/predictions
200
b'{"status":true}'


In [24]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/is-completed"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
print(response.content)

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/is-completed
b'false'


## Iteration 4

In [25]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/training-data"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
print(response.status_code)
print(response.content)
training_df = pd.DataFrame(response.json().get('training_data'))
shape = response.json().get('shape')

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/training-data
200
b'{"shape":[712,1597],"training_data":[{"interactionid":64476,"uid":47,"iid":507,"ts":885804123},{"interactionid":64477,"uid":47,"iid":296,"ts":885805093},{"interactionid":64478,"uid":47,"iid":1084,"ts":885805554},{"interactionid":64479,"uid":633,"iid":995,"ts":885806710},{"interactionid":64480,"uid":633,"iid":1,"ts":885806710},{"interactionid":64481,"uid":633,"iid":1452,"ts":885806779},{"interactionid":64482,"uid":633,"iid":988,"ts":885806797},{"interactionid":64483,"uid":633,"iid":301,"ts":885806823},{"interactionid":64484,"uid":633,"iid":1492,"ts":885806823},{"interactionid":64485,"uid":633,"iid":1469,"ts":885806862},{"interactionid":64486,"uid":633,"iid":1365,"ts":885806883},{"interactionid":64487,"uid":633,"iid":738,"ts":885807010},{"interactionid":64488,"uid":633,"iid":1465,"ts":885807035},{"interactionid":64489,"uid":633,"iid":1417,"ts":885807035},

In [26]:
from streamsightv2.matrix import InteractionMatrix

training_im = InteractionMatrix(training_df, item_ix='iid', user_ix='uid', timestamp_ix='ts', shape=shape)
external_model.fit(training_im)

X after decay:  [[2.74157741e-69 2.74211690e-69 2.74297394e-69 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 6.04653276e-27 3.11209300e-64 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 ...
 [0.00000000e+00 4.43459789e-01 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]]
DEBUG - Fitting TARSItemKNNLiu complete - Took 0.352s


TARSItemKNNLiu(K=100)

In [27]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/unlabeled-data"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
ul_df = pd.DataFrame(response.json().get('unlabeled_data'))
shape = response.json().get('shape')
ul_df

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/unlabeled-data


interactionid  uid  iid         ts
0             75303   48   -1  888396828
1             75304   48   -1  888396828
2             75305   48   -1  888396828
3             75306   48   -1  888396966
4             75307   48   -1  888396967
...             ...  ...  ...        ...
5945          83432  679   -1  890939697
5946          83433  679   -1  890939697
5947          83434  679   -1  890939753
5948          83435  679   -1  890939815
5949          83436  433   -1  890956632

[5950 rows x 4 columns]

In [28]:
ul_im = InteractionMatrix(ul_df, item_ix='iid', user_ix='uid', timestamp_ix='ts', shape=shape)
prediction = external_model.predict(training_im, ul_im)
print(prediction.toarray())
matrix_dict = {
    'data': prediction.data.tolist(),
    'indices': prediction.indices.tolist(),
    'indptr': prediction.indptr.tolist(),
    'shape': prediction.shape
}

DEBUG - Performing items_in comparison
In ItemKNNIncremental _predict:  [[4.96388530e-26 1.16916704e-25 7.99734961e-26 ... 1.11152105e-26
  1.39037970e-26 1.39037970e-26]
 [4.38817609e-11 9.50186017e-10 6.31256823e-10 ... 1.63104144e-10
  2.04023746e-10 2.04023746e-10]
 [1.13271500e-67 5.29524526e-62 4.29299883e-62 ... 1.40741570e-62
  1.76049895e-62 1.76049895e-62]
 ...
 [4.93094456e-05 7.53632474e+00 1.72532483e-01 ... 4.20997763e-01
  6.10736624e-01 6.10736624e-01]
 [3.25242039e-03 4.50160946e+00 4.80341900e-02 ... 1.34395796e-01
  2.81669477e-01 3.80889018e-01]
 [0.00000000e+00 1.52962997e+00 4.78631975e-02 ... 7.26327702e-02
  9.08548952e-02 9.08548952e-02]]
Max user ID:  784
Max item ID:  0
X.shape:  [712, 1597]
Intended shape:  (784, 1597)
Predict frame:        interactionid  uid  iid         ts  interactionid
0                 0   48   -1  888396828          75303
1                 1   48   -1  888396828          75304
2                 2   48   -1  888396828          75305
3  

In [29]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/predictions"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.post(url, json=matrix_dict)
print(response.status_code)
print(response.content)

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/predictions
200
b'{"status":true}'


In [30]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/is-completed"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
print(response.content)

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/is-completed
b'false'


## Iteration 5

In [31]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/training-data"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
print(response.status_code)
print(response.content)
training_df = pd.DataFrame(response.json().get('training_data'))
shape = response.json().get('shape')

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/training-data
200
b'{"shape":[784,1626],"training_data":[{"interactionid":75303,"uid":48,"iid":995,"ts":888396828},{"interactionid":75304,"uid":48,"iid":1572,"ts":888396828},{"interactionid":75305,"uid":48,"iid":1464,"ts":888396828},{"interactionid":75306,"uid":48,"iid":1592,"ts":888396966},{"interactionid":75307,"uid":48,"iid":1585,"ts":888396967},{"interactionid":75308,"uid":48,"iid":569,"ts":888397542},{"interactionid":75309,"uid":48,"iid":1479,"ts":888397542},{"interactionid":75310,"uid":48,"iid":319,"ts":888397946},{"interactionid":75311,"uid":48,"iid":605,"ts":888397981},{"interactionid":75312,"uid":48,"iid":436,"ts":888398069},{"interactionid":75313,"uid":48,"iid":861,"ts":888398069},{"interactionid":75314,"uid":48,"iid":917,"ts":888398087},{"interactionid":75315,"uid":48,"iid":18,"ts":888398104},{"interactionid":75316,"uid":48,"iid":603,"ts":888398123},{"interactio

In [32]:
from streamsightv2.matrix import InteractionMatrix

training_im = InteractionMatrix(training_df, item_ix='iid', user_ix='uid', timestamp_ix='ts', shape=shape)
external_model.fit(training_im)

X after decay:  [[2.56638542e-82 2.56689043e-82 2.56769271e-82 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [8.29490357e-04 5.66014786e-40 2.91322436e-77 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 ...
 [0.00000000e+00 4.33389416e-02 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]
 [3.38101301e-01 3.28937810e-01 3.36960572e-01 ... 0.00000000e+00
  0.00000000e+00 0.00000000e+00]]
DEBUG - Fitting TARSItemKNNLiu complete - Took 0.204s


TARSItemKNNLiu(K=100)

In [33]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/unlabeled-data"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
ul_df = pd.DataFrame(response.json().get('unlabeled_data'))
shape = response.json().get('shape')
ul_df

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/unlabeled-data


interactionid  uid  iid         ts
0              83437    7   -1  890979062
1              83438    7   -1  890979199
2              83439    7   -1  890979470
3              83440    7   -1  890979634
4              83441    7   -1  890979947
...              ...  ...  ...        ...
11199          99995  942   -1  893286638
11200          99996  942   -1  893286638
11201          99997  942   -1  893286638
11202          99998  942   -1  893286638
11203          99999  942   -1  893286638

[11204 rows x 4 columns]

In [34]:
ul_im = InteractionMatrix(ul_df, item_ix='iid', user_ix='uid', timestamp_ix='ts', shape=shape)
prediction = external_model.predict(training_im, ul_im)
print(prediction.toarray())
matrix_dict = {
    'data': prediction.data.tolist(),
    'indices': prediction.indices.tolist(),
    'indptr': prediction.indptr.tolist(),
    'shape': prediction.shape
}

DEBUG - Performing items_in comparison
In ItemKNNIncremental _predict:  [[1.95828809e-38 3.28129342e-13 1.95829752e-38 ... 8.44043394e-88
  0.00000000e+00 3.30701891e-15]
 [2.40544756e-01 2.31917069e-01 2.35837874e-01 ... 1.49218971e-43
  4.13424352e-08 1.87196281e-24]
 [1.15629809e-74 1.13613274e-74 1.15630366e-74 ... 5.45261565e-82
  0.00000000e+00 0.00000000e+00]
 ...
 [2.59551158e-01 3.89951862e-01 2.59552408e-01 ... 4.40537711e-02
  0.00000000e+00 4.21133874e-04]
 [2.86356823e-01 2.83042417e-01 2.86145128e-01 ... 0.00000000e+00
  0.00000000e+00 5.84486720e-03]
 [1.60149846e+01 1.57683114e+01 1.60156243e+01 ... 2.74121614e-01
  0.00000000e+00 5.13552802e-03]]
Max user ID:  943
Max item ID:  0
X.shape:  [784, 1626]
Intended shape:  (943, 1626)
Predict frame:         interactionid  uid  iid         ts  interactionid
0                  0    7   -1  890979062          83437
1                  1    7   -1  890979199          83438
2                  2    7   -1  890979470          83439

In [35]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/predictions"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.post(url, json=matrix_dict)
print(response.status_code)
print(response.content)

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/predictions
200
b'{"status":true}'


In [36]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/algorithms/{algorithm_id}/is-completed"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id, algorithm_id=algorithm_id)}"
print(url)
response = requests.get(url)
print(response.content)

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/algorithms/bdd640fb-0667-4ad1-9c80-317fa3b1799d/is-completed
b'true'


## Evaluation Metrics

In [37]:
import requests

# Define the base URL and endpoint
base_url = "http://localhost:8000"
endpoint = "/streams/{stream_id}/metrics"



# Construct the full URL
url = f"{base_url}{endpoint.format(stream_id=stream_id)}"
print(url)
response = requests.get(url)
print(response.content)

http://localhost:8000/streams/9072052c-4e08-4a50-9f51-e6b3f511d741/metrics
b'{"micro_metrics":[{"algorithm_name":"ta-item-knn","algorithm_id":"bdd640fb-0667-4ad1-9c80-317fa3b1799d","metric":"DCGK_100","micro_score":3.3930815007162205,"num_user":968},{"algorithm_name":"ta-item-knn","algorithm_id":"bdd640fb-0667-4ad1-9c80-317fa3b1799d","metric":"HitK_100","micro_score":0.13804752066115702,"num_user":96800},{"algorithm_name":"ta-item-knn","algorithm_id":"bdd640fb-0667-4ad1-9c80-317fa3b1799d","metric":"NDCGK_100","micro_score":0.25858635427321475,"num_user":968},{"algorithm_name":"ta-item-knn","algorithm_id":"bdd640fb-0667-4ad1-9c80-317fa3b1799d","metric":"PrecisionK_100","micro_score":0.13804752066115722,"num_user":968},{"algorithm_name":"ta-item-knn","algorithm_id":"bdd640fb-0667-4ad1-9c80-317fa3b1799d","metric":"RecallK_100","micro_score":0.3075566574300234,"num_user":968}],"macro_metrics":[{"algorithm_name":"ta-item-knn","algorithm_id":"bdd640fb-0667-4ad1-9c80-317fa3b1799d","metric":"D

In [38]:
# import json
response_data = response.json()
# Display Micro Metrics
print("Micro Metrics:")
for metric in response_data["micro_metrics"]:
    print(f"Algorithm: {metric['algorithm_name']} (ID: {metric['algorithm_id']})")
    print(f"  Metric: {metric['metric']}")
    print(f"  Micro Score: {metric['micro_score']}")
    print(f"  Number of Users: {metric['num_user']}\n")

# Display Macro Metrics
print("Macro Metrics:")
for metric in response_data["macro_metrics"]:
    print(f"Algorithm: {metric['algorithm_name']} (ID: {metric['algorithm_id']})")
    print(f"  Metric: {metric['metric']}")
    print(f"  Macro Score: {metric['macro_score']}")
    print(f"  Number of Windows: {metric['num_window']}\n")

Micro Metrics:
Algorithm: ta-item-knn (ID: bdd640fb-0667-4ad1-9c80-317fa3b1799d)
  Metric: DCGK_100
  Micro Score: 3.3930815007162205
  Number of Users: 968

Algorithm: ta-item-knn (ID: bdd640fb-0667-4ad1-9c80-317fa3b1799d)
  Metric: HitK_100
  Micro Score: 0.13804752066115702
  Number of Users: 96800

Algorithm: ta-item-knn (ID: bdd640fb-0667-4ad1-9c80-317fa3b1799d)
  Metric: NDCGK_100
  Micro Score: 0.25858635427321475
  Number of Users: 968

Algorithm: ta-item-knn (ID: bdd640fb-0667-4ad1-9c80-317fa3b1799d)
  Metric: PrecisionK_100
  Micro Score: 0.13804752066115722
  Number of Users: 968

Algorithm: ta-item-knn (ID: bdd640fb-0667-4ad1-9c80-317fa3b1799d)
  Metric: RecallK_100
  Micro Score: 0.3075566574300234
  Number of Users: 968

Macro Metrics:
Algorithm: ta-item-knn (ID: bdd640fb-0667-4ad1-9c80-317fa3b1799d)
  Metric: DCGK_100
  Macro Score: 3.3452696429189137
  Number of Windows: 5

Algorithm: ta-item-knn (ID: bdd640fb-0667-4ad1-9c80-317fa3b1799d)
  Metric: HitK_100
  Macro Scor